In [2]:
import pandas as pd
import os

In [3]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "sales/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [5]:
# base cols RegionID,SizeRank,RegionName,RegionType,StateName

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        # ignore monthly data for now since it is redundant
        if "monthly" in filename:
            continue

        if "_sfrcondo_" in filename:
            cur_df["Home Type"] = "all homes"
        elif "_sfr_" in filename:
            cur_df["Home Type"] = "SFR"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename
        seasonally_adjusted = "_sa_" in filename

        if "_median_sale_to_list_" in filename:
            col_name = "Median Sale to List Ratio"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        elif "_mean_sale_to_list_" in filename:
            col_name = "Mean Sale to List Ratio"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        elif "_median_sale_price_" in filename:
            col_name = "Median Sale Price"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        elif "_pct_sold_above_list_" in filename:
            col_name = "% Sold Above List"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        elif "_pct_sold_below_list_" in filename:
            col_name = "% Sold Below List"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        elif "_sales_count_now_" in filename:
            col_name = "Nowcast"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        data_frames.append(cur_df)


def get_combined_df(data_frames):
    combined_df = None
    if len(data_frames) > 1:
        # iterate over dataframes and merge or concat
        combined_df = data_frames[0]
        for i in range(1, len(data_frames)):
            cur_df = data_frames[i]
            combined_df = pd.merge(
                combined_df,
                cur_df,
                on=[
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    "Date",
                ],
                how="outer",
                suffixes=("", "_" + str(i)),
            )
    elif len(data_frames) == 1:
        combined_df = data_frames[0]

    return combined_df


combined_df = get_combined_df(data_frames)
# iterate over rows of combined df and coalesce column values across columns that start with "Median Sale Price"
columns_to_coalesce = [
    "Mean Sale to List Ratio (Smoothed)"
    "Median Sale to List Ratio"
    "Median Sale Price"
    "% Sold Below List (Smoothed)",
    "Median Sale Price (Smoothed) (Seasonally Adjusted)",
    "% Sold Below List",
    "Median Sale Price (Smoothed)",
    "Median Sale to List Ratio (Smoothed)",
    "% Sold Above List",
    "Nowcast",
    "Mean Sale to List Ratio",
    "% Sold Above List (Smoothed)",
]

for index, row in combined_df.iterrows():
    for col in combined_df.columns:
        for column_to_coalesce in columns_to_coalesce:
            if column_to_coalesce in col and "_" in col:
                if not pd.isna(row[col]):
                    combined_df.at[index, column_to_coalesce] = row[col]

# remove columns with underscores
combined_df = combined_df[[col for col in combined_df.columns if "_" not in col]]

combined_df

processing Metro_mean_sale_to_list_uc_sfrcondo_sm_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_week.csv
processing Metro_median_sale_price_uc_sfr_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_sm_month.csv
processing Metro_median_sale_price_uc_sfr_sm_sa_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_month.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfr_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_sm_month.csv
processing Metro_pct_sold_above_list_uc_sfrcondo_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_sa_month.csv
processing Metro_sales_count_now_uc_sfrcondo_month.csv
processing Metro_pct_sold_above_list_uc_sfrcondo_week.csv
processing Metro_mean_sale_to_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_month.csv
proc

RegionID  SizeRank     RegionName RegionType StateName  Home Type  \
0         102001         0  United States    country       NaN        SFR   
1         102001         0  United States    country       NaN        SFR   
2         102001         0  United States    country       NaN        SFR   
3         102001         0  United States    country       NaN        SFR   
4         102001         0  United States    country       NaN        SFR   
...          ...       ...            ...        ...       ...        ...   
504603    845167       296     Ottawa, IL        msa        IL  all homes   
504604    845167       296     Ottawa, IL        msa        IL  all homes   
504605    845167       296     Ottawa, IL        msa        IL  all homes   
504606    845167       296     Ottawa, IL        msa        IL  all homes   
504607    845167       296     Ottawa, IL        msa        IL  all homes   

              Date  Mean Sale to List Ratio (Smoothed)  \
0       2008-02-02                                 NaN   
1       2008-02-09                                 NaN   
2       2008-02-16                                 NaN   
3       2008-02-23                                 NaN   
4       2008-02-29                                 NaN   
...            ...                                 ...   
504603  2023-07-31                            0.976219   
504604  2023-08-31                            0.971893   
504605  2023-09-30                            0.968028   
504606  2023-10-31                            0.962485   
504607  2023-11-30                            0.967126   

        Median Sale to List Ratio  Median Sale Price  \
0                             NaN           172000.0   
1                             NaN           165400.0   
2                             NaN           168000.0   
3                             NaN           165000.0   
4                             NaN                NaN   
...                           ...                ...   
504603                        NaN                NaN   
504604                        NaN                NaN   
504605                        NaN                NaN   
504606                        NaN                NaN   
504607                        NaN                NaN   

        % Sold Below List (Smoothed)  \
0                                NaN   
1                                NaN   
2                                NaN   
3                                NaN   
4                                NaN   
...                              ...   
504603                      0.554969   
504604                      0.541090   
504605                      0.531140   
504606                      0.558836   
504607                      0.539226   

        Median Sale Price (Smoothed) (Seasonally Adjusted)  % Sold Below List  \
0                                                     NaN                 NaN   
1                                                     NaN                 NaN   
2                                                     NaN                 NaN   
3                                                     NaN                 NaN   
4                                                     NaN                 NaN   
...                                                   ...                 ...   
504603                                           127574.0            0.491379   
504604                                           125089.0            0.602041   
504605                                           127199.0            0.500000   
504606                                           131159.0            0.574468   
504607                                           129291.0            0.543210   

        Median Sale Price (Smoothed)  Median Sale to List Ratio (Smoothed)  \
0                                NaN                                   NaN   
1                                NaN                                   NaN   
2                        

In [6]:
final_df = combined_df
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df.sort_values(by=["Region ID", "Home Type", "Date"])

Region ID  Size Rank         Region Region Type State  Home Type  \
0          102001          0  United States     country   NaN        SFR   
1          102001          0  United States     country   NaN        SFR   
2          102001          0  United States     country   NaN        SFR   
3          102001          0  United States     country   NaN        SFR   
4          102001          0  United States     country   NaN        SFR   
...           ...        ...            ...         ...   ...        ...   
504603     845167        296     Ottawa, IL         msa    IL  all homes   
504604     845167        296     Ottawa, IL         msa    IL  all homes   
504605     845167        296     Ottawa, IL         msa    IL  all homes   
504606     845167        296     Ottawa, IL         msa    IL  all homes   
504607     845167        296     Ottawa, IL         msa    IL  all homes   

              Date  Mean Sale to List Ratio (Smoothed)  \
0       2008-02-02                                 NaN   
1       2008-02-09                                 NaN   
2       2008-02-16                                 NaN   
3       2008-02-23                                 NaN   
4       2008-02-29                                 NaN   
...            ...                                 ...   
504603  2023-07-31                            0.976219   
504604  2023-08-31                            0.971893   
504605  2023-09-30                            0.968028   
504606  2023-10-31                            0.962485   
504607  2023-11-30                            0.967126   

        Median Sale to List Ratio  Median Sale Price  \
0                             NaN           172000.0   
1                             NaN           165400.0   
2                             NaN           168000.0   
3                             NaN           165000.0   
4                             NaN                NaN   
...                           ...                ...   
504603                        NaN                NaN   
504604                        NaN                NaN   
504605                        NaN                NaN   
504606                        NaN                NaN   
504607                        NaN                NaN   

        % Sold Below List (Smoothed)  \
0                                NaN   
1                                NaN   
2                                NaN   
3                                NaN   
4                                NaN   
...                              ...   
504603                      0.554969   
504604                      0.541090   
504605                      0.531140   
504606                      0.558836   
504607                      0.539226   

        Median Sale Price (Smoothed) (Seasonally Adjusted)  % Sold Below List  \
0                                                     NaN                 NaN   
1                                                     NaN                 NaN   
2                                                     NaN                 NaN   
3                                                     NaN                 NaN   
4                                                     NaN                 NaN   
...                                                   ...                 ...   
504603                                           127574.0            0.491379   
504604                                           125089.0            0.602041   
504605                                           127199.0            0.500000   
504606                                           131159.0            0.574468   
504607                                           129291.0            0.543210   

        Median Sale Price (Smoothed)  Median Sale to List Ratio (Smoothed)  \
0                                NaN                                   NaN   
1                                NaN                                   NaN   
2                                NaN 

In [7]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)